In [1]:
from google.colab import drive
drive.mount('/content/drive/')

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [1]:
%%capture
!pip install transformers

In [2]:
import torch
import numpy as np
import pandas as pd
import torch.nn as nn

import transformers
from sklearn.metrics import *
from transformers import AdamW
from tqdm.notebook import tqdm
from scipy.special import softmax
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split as tts
from transformers import BertTokenizerFast, BertConfig, BertForSequenceClassification, AutoModel
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler

In [3]:
# Define the device
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

#### Download

In [4]:
cd drive/My Drive/Colab Notebooks/experiments

/content/drive/My Drive/Colab Notebooks/experiments


In [5]:
# Download humor detection data
# Paper: https://arxiv.org/abs/2004.12765
data = pd.read_csv("data/moh-x.csv")
print("\nThere are", len(data), "sentences")

# Use the standard text/label columns
# Create labels: 1 --> humorous, 0 --> not humorous
data["label"] = data["label"].apply(int)
data.head()


There are 647 sentences


arg1  arg2  ... verb_idx label
0  knowledge   NaN  ...        1     1
1       cost   NaN  ...        1     1
2        tax   NaN  ...        4     1
3  immigrant   NaN  ...        4     1
4   interest   NaN  ...        4     1

[5 rows x 6 columns]

#### Split to training, validation and test



In [22]:
%%time

#from simpletransformers.seq2seq import Seq2SeqModel

test_df = pd.read_csv("stockholm/bert_code/mohx_bert_subs/mohx_tp.csv")
test_df = test_df.rename(columns={"correct_label": "label"})
test_df = test_df[["sentence", "label"]]

CPU times: user 6.81 ms, sys: 1.28 ms, total: 8.1 ms
Wall time: 10.3 ms


In [23]:
test_df.head()

sentence  label
0                        A hot soup will revive me .      1
1                   He revived this style of opera .      1
2   They clawed their way to the top of the mount...      1
3   We rotate the crops so as to maximize the use...      1
4   She designed a good excuse for not attending ...      1

In [26]:
# Use a subset for quick experiments
#subset_data = data[:10000]

# Split to train, val and test
train, test = tts(data[["sentence", "label"]], random_state=42, test_size=0.1)
train, val = tts(train, random_state=42, test_size=test_df.shape[0])

#### Tokenize and encode with BERT tokenizer

In [8]:
!pip install sentencepiece

In [9]:
from transformers import XLMRobertaForSequenceClassification

output_dir = 'stockholm/xlm_code/mohx_xlmroberta/xlm-roberta_model_save'

print(output_dir)

stockholm/xlm_code/mohx_xlmroberta/xlm-roberta_model_save


In [12]:
from transformers import XLMRobertaTokenizer
import torch
# Load the BERT tokenizer.
print('Loading XLMRobertaTokenizer...')
bert_tokenizer = XLMRobertaTokenizer.from_pretrained(output_dir)
model_e = XLMRobertaForSequenceClassification.from_pretrained(output_dir, num_labels = 2, output_attentions = True, output_hidden_states = True,)

Loading XLMRobertaTokenizer...


Some weights of the model checkpoint at stockholm/xlm_code/mohx_xlmroberta/xlm-roberta_model_save were not used when initializing XLMRobertaForSequenceClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing XLMRobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [11]:
# Construct a BERT tokenizer based on WordPiece
bert_tokenizer = BertTokenizerFast.from_pretrained('bert-base-uncased')

In [13]:
# A sanity check of the tokenizer
encoded_instance = bert_tokenizer.batch_encode_plus([train.iloc[0].sentence], padding=True)
print(encoded_instance)

{'input_ids': [[0, 581, 104, 79099, 33, 332, 1924, 21407, 297, 3934, 70, 17155, 6, 5, 2]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]]}


In [14]:
print("Original text:", train.iloc[0].sentence)
print("BERT BPEs:", bert_tokenizer.convert_ids_to_tokens(encoded_instance["input_ids"][0]))

Original text:  The drunken man staggered into the room .
BERT BPEs: ['<s>', '▁The', '▁d', 'runk', 'en', '▁man', '▁sta', 'gger', 'ed', '▁into', '▁the', '▁room', '▁', '.', '</s>']


In [27]:
# Set max_len to the maximum length of the training data 
max_len = max([len(bert_tokenizer.encode(s)) for s in train.sentence.to_list()])
print("The maximum sentence length in training based on BERT BPEs is", max_len)

The maximum sentence length in training based on BERT BPEs is 25


In [28]:
# Tokenize and encode sentences in each set
x_train = bert_tokenizer.batch_encode_plus(
    train.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)
x_val = bert_tokenizer.batch_encode_plus(
    val.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)
x_test = bert_tokenizer.batch_encode_plus(
    test_df.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)

In [29]:
# Convert lists to tensors in order to feed them to our PyTorch model
train_seq = torch.tensor(x_train['input_ids'])
train_mask = torch.tensor(x_train['attention_mask'])
train_y = torch.tensor(train.label.tolist())

val_seq = torch.tensor(x_val['input_ids'])
val_mask = torch.tensor(x_val['attention_mask'])
val_y = torch.tensor(val.label.tolist())

test_seq = torch.tensor(x_test['input_ids'])
test_mask = torch.tensor(x_test['attention_mask'])
test_y = torch.tensor(test.label.tolist())

In [30]:
batch_size = 32

# Create a dataloader for each set

# TensorDataset: Creates a PyTorch dataset object to load data from
train_data = TensorDataset(train_seq, train_mask, train_y)
# RandomSampler: specify the sequence of indices/keys used in data loading
train_sampler = RandomSampler(train_data)
# DataLoader: a Python iterable over a dataset
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=batch_size)

val_data = TensorDataset(val_seq, val_mask, val_y)
val_sampler = SequentialSampler(val_data)
val_dataloader = DataLoader(val_data, sampler=val_sampler, batch_size=batch_size)

test_data = TensorDataset(test_seq, test_mask, test_y)
test_sampler = SequentialSampler(test_data)
test_dataloader = DataLoader(test_data, sampler=test_sampler, batch_size=1)

AssertionError: ignored

## Build and train the model

In [15]:
# Define which BERT model to use
# We will use BERT base pre-trained on uncased text
model_name = "bert-base-uncased"
# The BertForSequenceClassification class creates a model with BERT and a classifier on top
# The classifier is a linear layer with two outputs (two is the default, if you have more labels change the config)
# It uses the CrossEntropyLoss from PyTorch
# from_pretrained() is used to load pre-trained weights
model = BertForSequenceClassification.from_pretrained(model_name, output_attentions=True)

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.seq_relationship.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [16]:
# Training method
def training():
  # Set to train mode
  model.train()
  total_loss, total_accuracy = 0, 0
  # Iterate through the training batches
  for batch in tqdm(train_dataloader, desc="Iteration"):    
    # Push the batch to gpu
    batch = [r.to(device) for r in batch] 
    sent_id, mask, labels = batch
    # Clear gradients 
    model.zero_grad()
    # Get model outputs
    outputs = model(sent_id, attention_mask=mask, labels=labels)
    # Get loss
    loss = outputs.loss
    # Add to the total loss
    total_loss = total_loss + loss
    # Backward pass to calculate the gradients
    loss.backward()
    # Update parameters
    optimizer.step()
  # Compute the training loss of the epoch
  epoch_loss = total_loss / len(train_dataloader)

  return epoch_loss

In [17]:
# Evaluation method
def evaluate():  
  print("\nEvaluating...")  
  # Set to eval mode
  model.eval()
  total_loss, total_accuracy = 0, 0
  predictions, targets = [], []
  # Iterate through the validation batches
  for batch in val_dataloader:
    # Push the batch to gpu
    batch = [t.to(device) for t in batch]
    sent_id, mask, labels = batch
    # Save the gold labels to use them for evaluation
    targets.extend(labels.detach().cpu().numpy())
    # Deactivate autograd
    with torch.no_grad():
      # Get model outputs
      outputs = model(sent_id, attention_mask=mask, labels=labels)
      # Get loss
      loss = outputs.loss
      total_loss = total_loss + loss
      # Apply softmax to the output of the model
      output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
      # Get the index with the largest probability as the predicted label
      predictions.extend(np.argmax(output_probs, axis=1))
  # Compute the validation loss of the epoch
  epoch_loss = total_loss / len(val_dataloader)

  return epoch_loss, targets, predictions

In [18]:
# Push model to gpu
model = model.to(device)
# Define the optimizer and the learning rate
optimizer = AdamW(model.parameters(), lr = 2e-5)

best_val_loss = float('inf')
best_epoch = -1
train_losses=[]
val_losses=[]
epochs = 5
# Define the number of epochs to wait for early stopping
patience = 3

# Train the model
for epoch in range(epochs):     
  print('\n Epoch {:} / {:}'.format(epoch + 1, epochs))    
  train_loss = training()
  val_loss, val_targets, val_predictions = evaluate()

  train_losses.append(train_loss)
  val_losses.append(val_loss)

  print("\nTraining Loss:", train_loss)
  print("Validation Loss:", val_loss)
  # Calculate the validation F1 score for the current epoch
  f1 = f1_score(val_targets, val_predictions, average="binary")
  print("F1 score:", round(f1, 3))

  # Save the model with the best validation loss
  if val_loss < best_val_loss:
    best_val_loss = val_loss
    best_epoch = epoch
    torch.save(model.state_dict(), 'saved_weights.pt')

  # Early stopping
  if ((epoch - best_epoch) >= patience):
    print("No improvement in", patience, "epochs. Stopped training.")
    break



 Epoch 1 / 5




Evaluating...

Training Loss: tensor(0.6899, device='cuda:0', grad_fn=<DivBackward0>)
Validation Loss: tensor(0.6246, device='cuda:0')
F1 score: 0.229

 Epoch 2 / 5




Evaluating...

Training Loss: tensor(0.6375, device='cuda:0', grad_fn=<DivBackward0>)
Validation Loss: tensor(0.5316, device='cuda:0')
F1 score: 0.714

 Epoch 3 / 5




Evaluating...

Training Loss: tensor(0.4677, device='cuda:0', grad_fn=<DivBackward0>)
Validation Loss: tensor(0.3899, device='cuda:0')
F1 score: 0.76

 Epoch 4 / 5




Evaluating...

Training Loss: tensor(0.3451, device='cuda:0', grad_fn=<DivBackward0>)
Validation Loss: tensor(0.4267, device='cuda:0')
F1 score: 0.72

 Epoch 5 / 5




Evaluating...

Training Loss: tensor(0.2685, device='cuda:0', grad_fn=<DivBackward0>)
Validation Loss: tensor(0.4313, device='cuda:0')
F1 score: 0.681


In [19]:
# Save checkpoint to your drive
# Zip
#!zip saved_weights.zip  saved_weights.pt
# Mount
#from google.colab import drive
#drive.mount('/content/gdrive')
# Copy to your drive folder
#!cp -r saved_weights.zip /content/gdrive/MyDrive/

## Inference

#### Load the saved checkpoint

In [20]:
# Use this code to download the model saved in your drive 
# Add the id from the shareable link of the file 
# !gdown --id add_shareable_link_id
# !unzip saved_weights.zip

In [21]:
# Create the model
#model_e = BertForSequenceClassification.from_pretrained("bert-base-uncased", output_attentions=True)
# Load pre-trained weights
#checkpoint = torch.load("saved_weights.pt", map_location="cpu")
# Add them to the model
#model_e.load_state_dict(checkpoint)
#model_e = model_e.to(device)

In [22]:
!pip install sentencepiece

In [23]:
from transformers import XLMRobertaForSequenceClassification

output_dir = 'stockholm/xlm_code/mohx_xlmroberta/xlm-roberta_model_save'

print(output_dir)

stockholm/xlm_code/mohx_xlmroberta/xlm-roberta_model_save


In [24]:
from transformers import XLMRobertaTokenizer
import torch
# Load the BERT tokenizer.
print('Loading XLMRobertaTokenizer...')
bert_tokenizer = XLMRobertaTokenizer.from_pretrained(output_dir)
model_e = XLMRobertaForSequenceClassification.from_pretrained(output_dir, num_labels = 2, output_attentions = True, output_hidden_states = True,)

Loading XLMRobertaTokenizer...


Some weights of the model checkpoint at stockholm/xlm_code/mohx_xlmroberta/xlm-roberta_model_save were not used when initializing XLMRobertaForSequenceClassification: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
- This IS expected if you are initializing XLMRobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


#### Get predictions for test

In [25]:
# Predict for the test set and save the results
model_e = model_e.to(device)
model_e.eval()
test_predictions = []
test_targets = []
test_attentions = []
test_inputs = []

for batch in test_dataloader:
  batch = [t.to(device) for t in batch]
  sent_id, mask, labels = batch
  # Get gold labels
  test_targets.extend(labels.detach().cpu().numpy())
  # Get input words
  test_inputs.append(bert_tokenizer.convert_ids_to_tokens(sent_id.detach().cpu().numpy()[0]))
  with torch.no_grad():
    # Get predictions
    outputs = model_e(sent_id, attention_mask=mask)
    # Apply softmax to the outputs
    output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
    # Get the with the highest probability as the predicted label
    test_predictions.extend(np.argmax(output_probs, axis=1))
    # Get attention weights
    # Attention weights from all layers are returned in a tuple
    # The weights from each layer are in a tensor with shape (batch_size, attention_heads, max_len, max_len)
    test_attentions.append(outputs.attentions)

#### Evaluate

In [26]:
print("F1:", f1_score(test_targets, test_predictions, average="binary"))
print("ACC:", accuracy_score(test_targets, test_predictions))
print("RECALL:", recall_score(test_targets, test_predictions))
print("PRECISION:", average_precision_score(test_targets, test_predictions))
print("AUPR:", average_precision_score(test_targets, test_predictions))
print("AUC:", roc_auc_score(test_targets, test_predictions))

F1: 0.0
ACC: 0.4307692307692308
RECALL: 0.0
PRECISION: 0.5538461538461539
AUPR: 0.5538461538461539
AUC: 0.4827586206896552


In [27]:
#max pooling to generate a fixed sized sentence embedding


#Max Pooling - Take the max value over time for every dimension
def max_pooling(model_output, attention_mask):
    token_embeddings = model_output[0] #First element of model_output contains all token embeddings
    input_mask_expanded = attention_mask.resize_(token_embeddings.size())
    #input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    token_embeddings[input_mask_expanded == 0] = -1e9  # Set padding tokens to large negative value
    max_over_time = torch.max(token_embeddings, 1)[0]
    return max_over_time

def avg_pooling(model_output, attention_mask):
    token_embeddings = model_output[0] #First element of model_output contains all token embeddings
    input_mask_expanded = attention_mask.resize_(token_embeddings.size())
    #input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    token_embeddings[input_mask_expanded == 0] = -1e9  # Set padding tokens to large negative value
    avg_over_time = torch.mean(token_embeddings, 1)[0]
    return avg_over_time


#Sentences we want sentence embeddings for
sentences = ['The', 'stars', 'gravitate', 'towards', 'each', 'other.']

#Tokenize sentences
encoded_input = bert_tokenizer(sentences, padding=True, truncation=True, max_length=128, return_tensors='pt')
encoded_input = encoded_input.to(device)

#Compute token embeddings
with torch.no_grad():
    model_output = model_e(**encoded_input)

#Perform pooling. In this case, max pooling
sentence_embeddings = max_pooling(model_output, encoded_input['attention_mask'])
#avg_sentence_embeddings = avg_pooling(model_output, encoded_input['attention_mask'])


print("Sentence embeddings:")
print(sentence_embeddings)

Sentence embeddings:
tensor([0.2211, 0.3184, 0.0814, 0.2717, 0.8786, 1.0564], device='cuda:0')


In [28]:
# numpy implementation of argmax
from numpy import argmax

sentence_embeddings = sentence_embeddings.cpu()

# get argmax
result = argmax(sentence_embeddings)
print('arg max of %s: %d' % (sentence_embeddings, result))

arg max of tensor([0.2211, 0.3184, 0.0814, 0.2717, 0.8786, 1.0564]): 5


In [29]:
#CLS token of each input represents the sentence embedding


#Sentences we want sentence embeddings for
sentences = ['The', 'stars', 'gravitate', 'towards', 'each', 'other']


#Tokenize sentences
encoded_input = bert_tokenizer(sentences, padding=True, truncation=True, max_length=128, return_tensors='pt')
encoded_input = encoded_input.to(device)

#Compute token embeddings
with torch.no_grad():
    model_output = model_e(**encoded_input)
    #model_output = model_output.to(device)
    
sentence_embeddings = model_output[0][:,0] #Take the first token ([CLS]) from each sentence 

print("Sentence embeddings:")
print(sentence_embeddings)

Sentence embeddings:
tensor([-0.2066,  0.3184, -0.0368,  0.2717,  0.8786, -0.4190], device='cuda:0')


In [30]:
# numpy implementation of argmax
from numpy import argmax

sentence_embeddings = sentence_embeddings.cpu()

# get argmax
result = argmax(sentence_embeddings)
print('arg max of %s: %d' % (sentence_embeddings, result))

arg max of tensor([-0.2066,  0.3184, -0.0368,  0.2717,  0.8786, -0.4190]): 4


## Attention analysis

In [31]:
# Get attention heatmaps
import matplotlib
from IPython.core.display import display, HTML
def colorize(words, color_array):
    cmap=matplotlib.cm.Reds
    template = '<span class="barcode"; style="color: black; background-color: {}">{}</span>'
    colored_string = ''
    for word, color in zip(words, color_array):
        color = matplotlib.colors.rgb2hex(cmap(color)[:3])
        colored_string += template.format(color, '&nbsp' + word + '&nbsp')
    return colored_string

In [32]:
test_attentions1 = np.array(test_attentions)

In [33]:
test_attentions1.shape

(65, 12)

#### What does the CLS token attend to?




In [34]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [0,1,2]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    for h, head in enumerate(attention):
      print("Head", h+1)
      # Get the attention for the cls token
      encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
      encoded_tokens = encoded_tokens.to(device)
      with torch.no_grad():
        model_output1 = model_e(**encoded_tokens)
        tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
        tokens_embeddings = tokens_embeddings.cpu()
        cls_attentions = head[0]
        display(HTML(colorize(tokens, cls_attentions)))
        print("Tokens embeddings:")
        print(tokens_embeddings)
        arg = argmax(tokens_embeddings)
        print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1
Head 1


Tokens embeddings:
tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697]): 6
Head 2


Tokens embeddings:
tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697]): 6
Head 3


Tokens embeddings:
tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697]): 6
Head 4


Tokens embeddings:
tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697]): 6
Head 5


...

Tokens embeddings:
tensor([ 0.4040, -0.1522,  0.6992, -0.1026,  0.7223,  0.1860,  0.2765,  0.1018,
         0.0439,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1522,  0.6992, -0.1026,  0.7223,  0.1860,  0.2765,  0.1018,
         0.0439,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4
Head 9


Tokens embeddings:
tensor([ 0.4040, -0.1522,  0.6992, -0.1026,  0.7223,  0.1860,  0.2765,  0.1018,
         0.0439,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1522,  0.6992, -0.1026,  0.7223,  0.1860,  0.2765,  0.1018,
         0.0439,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4
Head 10


Tokens embeddings:
tensor([ 0.4040, -0.1522,  0.6992, -0.1026,  0.7223,  0.1860,  0.2765,  0.1018,
         0.0439,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1522,  0.6992, -0.1026,  0.7223,  0.1860,  0.2765,  0.1018,
         0.0439,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4
Head 11


Tokens embeddings:
tensor([ 0.4040, -0.1522,  0.6992, -0.1026,  0.7223,  0.1860,  0.2765,  0.1018,
         0.0439,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1522,  0.6992, -0.1026,  0.7223,  0.1860,  0.2765,  0.1018,
         0.0439,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4
Head 12


Tokens embeddings:
tensor([ 0.4040, -0.1522,  0.6992, -0.1026,  0.7223,  0.1860,  0.2765,  0.1018,
         0.0439,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1522,  0.6992, -0.1026,  0.7223,  0.1860,  0.2765,  0.1018,
         0.0439,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4


In [35]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [0,1,2,3,4,5,6,7,8,9,10]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697]): 6

Layer 2


Tokens embeddings:
tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697]): 6

Layer 3


Tokens embeddings:
tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697]): 6

Layer 4


Tokens embeddings:
tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  1.0073,  0.0354,  0.3246,  0.6460,  1.4596, -0.1087,
         0.3246, -0.1461,  0.1018,  0.0439,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697]): 6

Layer 5


...

Tokens embeddings:
tensor([ 0.4040, -0.1046,  0.1656, -0.2704,  0.5833, -0.0761,  0.3246,  0.1818,
         0.1018,  0.0439,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1046,  0.1656, -0.2704,  0.5833, -0.0761,  0.3246,  0.1818,
         0.1018,  0.0439,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4

Layer 9


Tokens embeddings:
tensor([ 0.4040, -0.1046,  0.1656, -0.2704,  0.5833, -0.0761,  0.3246,  0.1818,
         0.1018,  0.0439,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1046,  0.1656, -0.2704,  0.5833, -0.0761,  0.3246,  0.1818,
         0.1018,  0.0439,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4

Layer 10


Tokens embeddings:
tensor([ 0.4040, -0.1046,  0.1656, -0.2704,  0.5833, -0.0761,  0.3246,  0.1818,
         0.1018,  0.0439,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1046,  0.1656, -0.2704,  0.5833, -0.0761,  0.3246,  0.1818,
         0.1018,  0.0439,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4

Layer 11


Tokens embeddings:
tensor([ 0.4040, -0.1046,  0.1656, -0.2704,  0.5833, -0.0761,  0.3246,  0.1818,
         0.1018,  0.0439,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1046,  0.1656, -0.2704,  0.5833, -0.0761,  0.3246,  0.1818,
         0.1018,  0.0439,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4

Layer 12


Tokens embeddings:
tensor([ 0.4040, -0.1046,  0.1656, -0.2704,  0.5833, -0.0761,  0.3246,  0.1818,
         0.1018,  0.0439,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1046,  0.1656, -0.2704,  0.5833, -0.0761,  0.3246,  0.1818,
         0.1018,  0.0439,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4


In [36]:
# Select some sentences randomly
sent_index = [11,12,13,14,15,16,17,18,19,20]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([ 0.4040, -0.2584,  0.1930, -0.1530,  0.0936, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646,  0.0697, -0.0646,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.2584,  0.1930, -0.1530,  0.0936, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646,  0.0697, -0.0646,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697]): 6

Layer 2


Tokens embeddings:
tensor([ 0.4040, -0.2584,  0.1930, -0.1530,  0.0936, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646,  0.0697, -0.0646,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.2584,  0.1930, -0.1530,  0.0936, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646,  0.0697, -0.0646,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697]): 6

Layer 3


Tokens embeddings:
tensor([ 0.4040, -0.2584,  0.1930, -0.1530,  0.0936, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646,  0.0697, -0.0646,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.2584,  0.1930, -0.1530,  0.0936, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646,  0.0697, -0.0646,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697]): 6

Layer 4


Tokens embeddings:
tensor([ 0.4040, -0.2584,  0.1930, -0.1530,  0.0936, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646,  0.0697, -0.0646,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.2584,  0.1930, -0.1530,  0.0936, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646,  0.0697, -0.0646,  0.0697,  0.0697,  0.0697, -0.0646,
         0.0697]): 6

Layer 5


...

Tokens embeddings:
tensor([ 0.4040,  0.4334,  0.6883,  0.6889,  0.8189,  0.1018,  0.0439,  0.0697,
         0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  0.6883,  0.6889,  0.8189,  0.1018,  0.0439,  0.0697,
         0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4

Layer 9


Tokens embeddings:
tensor([ 0.4040,  0.4334,  0.6883,  0.6889,  0.8189,  0.1018,  0.0439,  0.0697,
         0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  0.6883,  0.6889,  0.8189,  0.1018,  0.0439,  0.0697,
         0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4

Layer 10


Tokens embeddings:
tensor([ 0.4040,  0.4334,  0.6883,  0.6889,  0.8189,  0.1018,  0.0439,  0.0697,
         0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  0.6883,  0.6889,  0.8189,  0.1018,  0.0439,  0.0697,
         0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4

Layer 11


Tokens embeddings:
tensor([ 0.4040,  0.4334,  0.6883,  0.6889,  0.8189,  0.1018,  0.0439,  0.0697,
         0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  0.6883,  0.6889,  0.8189,  0.1018,  0.0439,  0.0697,
         0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4

Layer 12


Tokens embeddings:
tensor([ 0.4040,  0.4334,  0.6883,  0.6889,  0.8189,  0.1018,  0.0439,  0.0697,
         0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040,  0.4334,  0.6883,  0.6889,  0.8189,  0.1018,  0.0439,  0.0697,
         0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4


In [37]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([-0.2853,  0.4334, -0.7529, -0.0408, -0.2584,  0.6460,  1.4596, -0.1087,
        -0.2584, -0.1461,  0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853,  0.4334, -0.7529, -0.0408, -0.2584,  0.6460,  1.4596, -0.1087,
        -0.2584, -0.1461,  0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 6

Layer 2


Tokens embeddings:
tensor([-0.2853,  0.4334, -0.7529, -0.0408, -0.2584,  0.6460,  1.4596, -0.1087,
        -0.2584, -0.1461,  0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853,  0.4334, -0.7529, -0.0408, -0.2584,  0.6460,  1.4596, -0.1087,
        -0.2584, -0.1461,  0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 6

Layer 3


Tokens embeddings:
tensor([-0.2853,  0.4334, -0.7529, -0.0408, -0.2584,  0.6460,  1.4596, -0.1087,
        -0.2584, -0.1461,  0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853,  0.4334, -0.7529, -0.0408, -0.2584,  0.6460,  1.4596, -0.1087,
        -0.2584, -0.1461,  0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 6

Layer 4


Tokens embeddings:
tensor([-0.2853,  0.4334, -0.7529, -0.0408, -0.2584,  0.6460,  1.4596, -0.1087,
        -0.2584, -0.1461,  0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853,  0.4334, -0.7529, -0.0408, -0.2584,  0.6460,  1.4596, -0.1087,
        -0.2584, -0.1461,  0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 6

Layer 5


...

Tokens embeddings:
tensor([-0.2853, -0.1046, -0.1244, -0.2704, -0.5105, -0.0761, -0.2584, -0.1457,
         0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.1046, -0.1244, -0.2704, -0.5105, -0.0761, -0.2584, -0.1457,
         0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 8

Layer 9


Tokens embeddings:
tensor([-0.2853, -0.1046, -0.1244, -0.2704, -0.5105, -0.0761, -0.2584, -0.1457,
         0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.1046, -0.1244, -0.2704, -0.5105, -0.0761, -0.2584, -0.1457,
         0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 8

Layer 10


Tokens embeddings:
tensor([-0.2853, -0.1046, -0.1244, -0.2704, -0.5105, -0.0761, -0.2584, -0.1457,
         0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.1046, -0.1244, -0.2704, -0.5105, -0.0761, -0.2584, -0.1457,
         0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 8

Layer 11


Tokens embeddings:
tensor([-0.2853, -0.1046, -0.1244, -0.2704, -0.5105, -0.0761, -0.2584, -0.1457,
         0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.1046, -0.1244, -0.2704, -0.5105, -0.0761, -0.2584, -0.1457,
         0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 8

Layer 12


Tokens embeddings:
tensor([-0.2853, -0.1046, -0.1244, -0.2704, -0.5105, -0.0761, -0.2584, -0.1457,
         0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.1046, -0.1244, -0.2704, -0.5105, -0.0761, -0.2584, -0.1457,
         0.1018,  0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 8


In [38]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [11, 12, 13, 14, 15, 16, 17, 18, 19, 20]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([-0.2853, -0.2584,  0.1930, -0.1530, -0.0761, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.2584,  0.1930, -0.1530, -0.0761, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 6

Layer 2


Tokens embeddings:
tensor([-0.2853, -0.2584,  0.1930, -0.1530, -0.0761, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.2584,  0.1930, -0.1530, -0.0761, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 6

Layer 3


Tokens embeddings:
tensor([-0.2853, -0.2584,  0.1930, -0.1530, -0.0761, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.2584,  0.1930, -0.1530, -0.0761, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 6

Layer 4


Tokens embeddings:
tensor([-0.2853, -0.2584,  0.1930, -0.1530, -0.0761, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.2584,  0.1930, -0.1530, -0.0761, -0.2868,  1.3393,  0.1018,
         0.0439, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 6

Layer 5


...

Tokens embeddings:
tensor([-0.2853,  0.4334, -0.6296,  0.6889,  0.8189,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853,  0.4334, -0.6296,  0.6889,  0.8189,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 4

Layer 9


Tokens embeddings:
tensor([-0.2853,  0.4334, -0.6296,  0.6889,  0.8189,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853,  0.4334, -0.6296,  0.6889,  0.8189,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 4

Layer 10


Tokens embeddings:
tensor([-0.2853,  0.4334, -0.6296,  0.6889,  0.8189,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853,  0.4334, -0.6296,  0.6889,  0.8189,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 4

Layer 11


Tokens embeddings:
tensor([-0.2853,  0.4334, -0.6296,  0.6889,  0.8189,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853,  0.4334, -0.6296,  0.6889,  0.8189,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 4

Layer 12


Tokens embeddings:
tensor([-0.2853,  0.4334, -0.6296,  0.6889,  0.8189,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853,  0.4334, -0.6296,  0.6889,  0.8189,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 4


In [39]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([ 0.4040,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889,  0.4546, -0.1057,
         0.1925,  0.9639,  0.0135,  0.1305,  1.4596,  0.6889,  0.0580,  0.1018,
         0.0439])
arg max of tensor([ 0.4040,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889,  0.4546, -0.1057,
         0.1925,  0.9639,  0.0135,  0.1305,  1.4596,  0.6889,  0.0580,  0.1018,
         0.0439]): 12

Layer 2


Tokens embeddings:
tensor([ 0.4040,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889,  0.4546, -0.1057,
         0.1925,  0.9639,  0.0135,  0.1305,  1.4596,  0.6889,  0.0580,  0.1018,
         0.0439])
arg max of tensor([ 0.4040,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889,  0.4546, -0.1057,
         0.1925,  0.9639,  0.0135,  0.1305,  1.4596,  0.6889,  0.0580,  0.1018,
         0.0439]): 12

Layer 3


Tokens embeddings:
tensor([ 0.4040,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889,  0.4546, -0.1057,
         0.1925,  0.9639,  0.0135,  0.1305,  1.4596,  0.6889,  0.0580,  0.1018,
         0.0439])
arg max of tensor([ 0.4040,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889,  0.4546, -0.1057,
         0.1925,  0.9639,  0.0135,  0.1305,  1.4596,  0.6889,  0.0580,  0.1018,
         0.0439]): 12

Layer 4


Tokens embeddings:
tensor([ 0.4040,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889,  0.4546, -0.1057,
         0.1925,  0.9639,  0.0135,  0.1305,  1.4596,  0.6889,  0.0580,  0.1018,
         0.0439])
arg max of tensor([ 0.4040,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889,  0.4546, -0.1057,
         0.1925,  0.9639,  0.0135,  0.1305,  1.4596,  0.6889,  0.0580,  0.1018,
         0.0439]): 12

Layer 5


...

Tokens embeddings:
tensor([ 0.4040, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
         0.0697,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
         0.0697,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4

Layer 9


Tokens embeddings:
tensor([ 0.4040, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
         0.0697,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
         0.0697,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4

Layer 10


Tokens embeddings:
tensor([ 0.4040, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
         0.0697,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
         0.0697,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4

Layer 11


Tokens embeddings:
tensor([ 0.4040, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
         0.0697,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
         0.0697,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4

Layer 12


Tokens embeddings:
tensor([ 0.4040, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
         0.0697,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697])
arg max of tensor([ 0.4040, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
         0.0697,  0.0697,  0.0697, -0.0646,  0.0697, -0.0646,  0.0697, -0.0646,
         0.0697]): 4


In [40]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([-0.2853,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889, -0.2691, -0.1057,
        -0.1532,  0.9639, -0.0562, -0.0645,  1.4596,  0.6889, -0.0446,  0.1018,
         0.0439])
arg max of tensor([-0.2853,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889, -0.2691, -0.1057,
        -0.1532,  0.9639, -0.0562, -0.0645,  1.4596,  0.6889, -0.0446,  0.1018,
         0.0439]): 12

Layer 2


Tokens embeddings:
tensor([-0.2853,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889, -0.2691, -0.1057,
        -0.1532,  0.9639, -0.0562, -0.0645,  1.4596,  0.6889, -0.0446,  0.1018,
         0.0439])
arg max of tensor([-0.2853,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889, -0.2691, -0.1057,
        -0.1532,  0.9639, -0.0562, -0.0645,  1.4596,  0.6889, -0.0446,  0.1018,
         0.0439]): 12

Layer 3


Tokens embeddings:
tensor([-0.2853,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889, -0.2691, -0.1057,
        -0.1532,  0.9639, -0.0562, -0.0645,  1.4596,  0.6889, -0.0446,  0.1018,
         0.0439])
arg max of tensor([-0.2853,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889, -0.2691, -0.1057,
        -0.1532,  0.9639, -0.0562, -0.0645,  1.4596,  0.6889, -0.0446,  0.1018,
         0.0439]): 12

Layer 4


Tokens embeddings:
tensor([-0.2853,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889, -0.2691, -0.1057,
        -0.1532,  0.9639, -0.0562, -0.0645,  1.4596,  0.6889, -0.0446,  0.1018,
         0.0439])
arg max of tensor([-0.2853,  0.1486,  0.6297, -0.0562,  0.5443,  0.6889, -0.2691, -0.1057,
        -0.1532,  0.9639, -0.0562, -0.0645,  1.4596,  0.6889, -0.0446,  0.1018,
         0.0439]): 12

Layer 5


...

Tokens embeddings:
tensor([-0.2853, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 4

Layer 9


Tokens embeddings:
tensor([-0.2853, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 4

Layer 10


Tokens embeddings:
tensor([-0.2853, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 4

Layer 11


Tokens embeddings:
tensor([-0.2853, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 4

Layer 12


Tokens embeddings:
tensor([-0.2853, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646])
arg max of tensor([-0.2853, -0.1891,  0.1703, -0.6576,  0.4633,  0.1018,  0.0439, -0.0646,
        -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646, -0.0646,
        -0.0646]): 4


#### Visualize attentions for specific types of grammatical errors

In [41]:
# Lack of Subject-Verb Agreement
sentence1 = "The stars gravitate towards each other."
# Pronoun Disagreement
sentence2 = "A hot soup will revive me."

In [42]:
# Encode the first sentence
encoded_sentence1 = bert_tokenizer.batch_encode_plus([sentence1], padding=True)

# Give as input to the model and get the outputs
inputs = torch.tensor(encoded_sentence1["input_ids"]).to(device)
att = torch.tensor(encoded_sentence1["attention_mask"]).to(device)
outputs = model_e(inputs, attention_mask=att)

In [43]:
# Get the predictions
output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
predictions = (np.argmax(output_probs, axis=1))
print(sentence1, ":", predictions[0])

The stars gravitate towards each other. : 0


In [44]:
# Visualize the attention heatmaps for the CLS token
tokens = bert_tokenizer.convert_ids_to_tokens(inputs.detach().cpu().numpy()[0])
for l in range(12):
  print("\nLayer", l+1)
  attention = np.squeeze(outputs.attentions[l].detach().cpu().numpy(), axis=0)
  cls_attentions = []
  for h, head in enumerate(attention):
    print("Head", h+1)
    # Get the attention for the cls token
    cls_attentions = head[0]
    display(HTML(colorize(tokens, cls_attentions)))


Layer 1
Head 1


Head 2


Head 3


Head 4


Head 5


...

Head 8


Head 9


Head 10


Head 11


Head 12


In [45]:
# Encode the second sentence
encoded_sentence2 = bert_tokenizer.batch_encode_plus([sentence2], padding=True)

# Give as input to the model and get the outputs
inputs = torch.tensor(encoded_sentence2["input_ids"]).to(device)
att = torch.tensor(encoded_sentence2["attention_mask"]).to(device)
outputs = model_e(inputs, attention_mask=att)

# Get the predictions
output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
predictions = (np.argmax(output_probs, axis=1))
print(sentence2, ":", predictions[0])

A hot soup will revive me. : 1


In [46]:
# Visualize the attention heatmaps for the CLS token
tokens = bert_tokenizer.convert_ids_to_tokens(inputs.detach().cpu().numpy()[0])
for l in range(12):
  print("\nLayer", l+1)
  attention = np.squeeze(outputs.attentions[l].detach().cpu().numpy(), axis=0)
  cls_attentions = []
  for h, head in enumerate(attention):
    print("Head", h+1)
    # Get the attention for the cls token
    cls_attentions = head[0]
    display(HTML(colorize(tokens, cls_attentions)))


Layer 1
Head 1


Head 2


Head 3


Head 4


Head 5


...

Head 8


Head 9


Head 10


Head 11


Head 12
